# Data Visualisation
----
## Scooter Registration by Fuel Type
First, I want to know whether the sales of electric scooters increase since September, 2012. The data I used is `reg_w.csv` from the `output` folder. As the number of registrations is for individual city, I sum up all cities each month. Then, I create a `ratio` column to show the proportion of electric scooters of all scooter registrations.

In [1]:
import pandas as pd
import plotly.graph_objs as go
import plotly.offline as py
from plotly.offline import iplot, init_notebook_mode
import plotly_express as px
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.dates as mdates
import numpy as np

init_notebook_mode(connected=True)

reg_w = pd.read_csv("output/reg_wide.csv", parse_dates=["time"], thousands=",")

reg_w_all = reg_w.resample("MS", on="time").sum()

reg_w_all["ratio"] = (
    reg_w_all["elec_reg"] / (reg_w_all["gas_reg"] + reg_w_all["elec_reg"])
) * 100

reg_w["ratio"] = (reg_w["elec_reg"] / (reg_w["gas_reg"] + reg_w["elec_reg"])) * 100


### Total Number of Scooters 
The stacked bar chart shows the total number of scooter registration by fuel type. The portions for electric scooters, coloured in blue, are too small to be observable initially. It can be seen that the number of scooters reduced noticably in September 2013, the reasons for which are unclear, and remained relatively constant afterwards. However, the proportion of electric scooters consistently grew. 

The line chart outlines the ratio of electric scooters of all, which increased from the 0.20% in September 2012 to 2.63% in Feburary 2020. The ratio grew increasingly until December 2019, which is the last month before the amount of subsidy is cut to half starting from 2020.

In [8]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(
    go.Bar(
        name="Electricity",
        marker_color="#1f78b4",
        x=list(reg_w_all.index),
        y=list(reg_w_all["elec_reg"]),
    ),
    secondary_y=False,
)

fig.add_trace(
    go.Bar(
        name="Gasoline",
        marker_color="#fbb4ae",
        x=list(reg_w_all.index),
        y=list(reg_w_all["gas_reg"]),
    ),
    secondary_y=False,
)

fig.add_trace(
    go.Scatter(
        marker_color="#238b45",
        marker_line_width=2,
        x=list(reg_w.resample("MS", on="time").sum().index),
        y=list(reg_w_all["ratio"]),
        showlegend=False,
    ),
    secondary_y=True,
)

fig.add_annotation(x="2015-08-01", y=13000000, text="<b>EPA and Local</b>")

fig.add_annotation(x="2012-09-01", y=15000000, text="<b>MOEA</b>")

fig.add_annotation(x="2019-12-01", y=15650000, text="<b>Cut</b>")


fig.update_annotations(
    dict(xref="x", yref="y", showarrow=True, arrowhead=7, ax=0, ay=-40)
)


fig.update_layout(
    title={
        "text": "<b>Total Scooter Registration</b>",
        "xanchor": "center",
        "x": 0.5,
        "yanchor": "top",
        "y": 0.97,
    },
    margin=dict(t=40, b=10),
    barmode="stack",
    width=1200,
    height=675,
    font=dict(size=14),
    legend_orientation="h",
    legend=dict(
        xanchor="right",
        yanchor="top",
        x=0.6,
        y=1,
        bgcolor="rgba(0,0,0,0)",
        font=dict(size=15),
    ),
    autosize=True,
)


fig.update_xaxes(tickfont=dict(size=12))

fig.update_yaxes(
    title_text="Total Registration",
    title=dict(font=dict(size=16)),
    secondary_y=False,
    tickfont=dict(size=12),
)

fig.update_yaxes(
    title_text="Ratio of Electric Scooter (%)",
    title=dict(font=dict(size=16)),
    secondary_y=True,
    tickfont=dict(size=12),
)

fig.show(config={"displaylogo": False}))

### Electric Scooter Ratios by City
Majority of the cities follow the similar upward patterns as the entire nation. 

In [3]:
fig = make_subplots(
    rows=5,
    cols=5,
    shared_yaxes=True,
    subplot_titles=sorted(reg_w["city"].unique().tolist()),
    vertical_spacing=0.08,
    horizontal_spacing=0.02,
    y_title="Ratio of electric scooter (%)",
)
palette = [
    "#e41a1c",
    "#377eb8",
    "#4daf4a",
    "#984ea3",
    "#ff7f00",
    "#ffff33",
    "#a65628",
    "#f781bf",
] * 3

row_num = 1
col_num = 1
num = 0
for city in sorted(reg_w["city"].unique().tolist()):
    num += 1
    # data = reg_w[reg_w['city']==city]
    for c in sorted(reg_w["city"].unique().tolist()):
        fig.add_trace(
            go.Scatter(
                x=reg_w[reg_w["city"] == c]["time"],
                y=reg_w[reg_w["city"] == c]["ratio"],
                marker_color="#7f7f7f",
                opacity=0.2,
                marker_size=0.2,
            ),
            row=row_num,
            col=col_num,
        )

    fig.add_trace(
        go.Scatter(
            x=reg_w[reg_w["city"] == city]["time"],
            y=reg_w[reg_w["city"] == city]["ratio"],
            marker_size=1.5,
            mode="lines",
            marker_color=palette[num],
        ),
        row=row_num,
        col=col_num,
    )
    col_num += 1
    if col_num > 5:
        row_num += 1
        col_num = 1

fig.update_layout(
    height=800,
    width=1200,
    showlegend=False,
    title=dict(
        text="<b>Electric scooter ratios by city</b>",
        xanchor="center",
        x=0.5,
        yanchor="top",
        y=0.99,
    ),
    font=dict(size=15),
    margin=dict(b=15, t=70),
)
fig.update_yaxes(range=[0, 6], tickfont=dict(size=12))
fig.update_xaxes(tickfont=dict(size=12))
fig.show()

## Subsidy

In [17]:
data = pd.read_csv('output/data.csv', parse_dates = ['time']).drop(columns='Unnamed: 0')
data.head(5)

time                      type           city  epa_app  moea_app  \
0 2012-09-01              New Purchase    Taipei City      NaN      18.0   
1 2012-09-01  Elimination and Purchase    Taipei City      NaN      19.0   
2 2012-09-01               Elimination    Taipei City      NaN       0.0   
3 2012-09-01              New Purchase  Taichung City      NaN      45.0   
4 2012-09-01  Elimination and Purchase  Taichung City      NaN      45.0   

   moea_amt  epa_amt  local_amt  
0     10000      NaN        NaN  
1     10000      NaN        NaN  
2     10000      NaN        NaN  
3     10000      NaN        NaN  
4     10000      NaN        NaN

In [84]:
sub = (
    data.groupby("type")
    .resample("MS", on="time")
    .sum()
    .reset_index()[["time", "type", "epa_app", "moea_app"]]
    .merge(
        data.groupby("type")
        .resample("MS", on="time")
        .mean()
        .reset_index()[["time", "type", "moea_amt", "epa_amt", "local_amt"]],
        on=["time", "type"],
    )
)
sub = sub[sub["type"] != "Elimination"]

sub.loc[sub["type"] != "Elimination", "moea_amt"] = 10000

sub.head(5)

time                      type  epa_app  moea_app  moea_amt  epa_amt  \
35 2012-09-01  Elimination and Purchase      0.0     309.0   10000.0      NaN   
36 2012-10-01  Elimination and Purchase      0.0     358.0   10000.0      NaN   
37 2012-11-01  Elimination and Purchase      0.0     231.0   10000.0      NaN   
38 2012-12-01  Elimination and Purchase      0.0     130.0   10000.0      NaN   
39 2013-01-01  Elimination and Purchase      0.0      75.0   10000.0      NaN   

    local_amt  
35        NaN  
36        NaN  
37        NaN  
38        NaN  
39        NaN

In [86]:
fig = make_subplots(
    rows=1,
    cols=2,
    shared_yaxes=True,
    subplot_titles=[
        "MOEA Subsidy for <br>New Purchase",
        "MOEA Subsidy for <br>Elimination and Purchase",
    ],
    vertical_spacing=0.05,
    horizontal_spacing=0.05,
)

fig.add_trace(
    go.Scatter(
        x=sub[sub["type"] == "New Purchase"]["time"],
        y=sub[sub["type"] == "New Purchase"]["moea_app"],
        marker_color="#ff6361",
    ),
    row=1,
    col=1,
)

fig.add_trace(
    go.Scatter(
        x=sub[sub["type"] == "Elimination and Purchase"]["time"],
        y=sub[sub["type"] == "Elimination and Purchase"]["moea_app"],
        marker_color="#488f31",
    ),
    row=1,
    col=2,
)

fig.add_trace(
    go.Bar(
        x=sub[sub["type"] == "New Purchase"]["time"],
        y=sub[sub["type"] == "New Purchase"]["moea_amt"],
        marker_color="#F9E79F",
    ),
    row=1,
    col=1,
)

fig.add_trace(
    go.Bar(
        x=sub[sub["type"] == "Elimination and Purchase"]["time"],
        y=sub[sub["type"] == "Elimination and Purchase"]["moea_amt"],
        marker_color="#F9E79F",
    ),
    row=1,
    col=2,
)

fig.update_layout(
    showlegend=False, width=1200, height=675,
)

fig.show()

In [87]:
fig = make_subplots(
    rows=1,
    cols=2,
    shared_yaxes=True,
    subplot_titles=[
        "EPA Subsidy for <br>New Purchase",
        "EPA Subsidy for <br>Elimination and Purchase",
    ],
    vertical_spacing=0.05,
    horizontal_spacing=0.05,
)

fig.add_trace(
    go.Scatter(
        x=sub[sub["type"] == "New Purchase"]["time"],
        y=sub[sub["type"] == "New Purchase"]["epa_app"],
        marker_color="#ff6361",
    ),
    row=1,
    col=1,
)

fig.add_trace(
    go.Scatter(
        x=sub[sub["type"] == "Elimination and Purchase"]["time"],
        y=sub[sub["type"] == "Elimination and Purchase"]["epa_app"],
        marker_color="#488f31",
    ),
    row=1,
    col=2,
)

fig.add_trace(
    go.Bar(
        x=sub[sub["type"] == "New Purchase"]["time"],
        y=sub[sub["type"] == "New Purchase"]["epa_amt"],
        marker_color="#D2B4DE",
    ),
    row=1,
    col=1,
)

fig.add_trace(
    go.Bar(
        x=sub[sub["type"] == "Elimination and Purchase"]["time"],
        y=sub[sub["type"] == "Elimination and Purchase"]["epa_amt"],
        marker_color="#D2B4DE",
    ),
    row=1,
    col=2,
)

fig.update_layout(
    showlegend=False, width=1200, height=675,
)

fig.show()

In [88]:
fig = make_subplots(
    rows=1,
    cols=2,
    shared_yaxes=True,
    subplot_titles=[
        "Local Subsidy for <br>New Purchase",
        "Local Subsidy for <br>Elimination and Purchase",
    ],
    vertical_spacing=0.05,
    horizontal_spacing=0.05,
)


fig.add_trace(
    go.Bar(
        x=sub[sub["type"] == "New Purchase"]["time"],
        y=sub[sub["type"] == "New Purchase"]["local_amt"],
        marker_color="#EDBB99",
    ),
    row=1,
    col=1,
)

fig.add_trace(
    go.Bar(
        x=sub[sub["type"] == "Elimination and Purchase"]["time"],
        y=sub[sub["type"] == "Elimination and Purchase"]["local_amt"],
        marker_color="#EDBB99",
    ),
    row=1,
    col=2,
)

fig.update_layout(
    showlegend=False, width=1200, height=675,
)

fig.show()

In [102]:
fig = make_subplots(
    rows=22,
    cols=2,
    shared_yaxes=True,
    subplot_titles=sorted(data["city"].unique().tolist()*2)
)

row_num = 1
num = 0
for city in sorted(data["city"].unique().tolist()):
    fig.add_trace(
        go.Bar(
            x=data[(data['city']==city) & (data['type']=='New Purchase')]['time'],
            y=data[(data['city']==city) & (data['type']=='New Purchase')]['local_amt']
        ),
        row = row_num,
        col = 1
    )

    fig.add_trace(
        go.Bar(
            x=data[(data['city']==city) & (data['type']=='Elimination and Purchase')]['time'],
            y=data[(data['city']==city) & (data['type']=='Elimination and Purchase')]['local_amt']
        ),
        row = row_num,
        col = 2
    )
    row_num += 1

fig.update_layout(showlegend=False, width=1200, height=3600)
fig.show()

In [105]:
data[(data['city']=='Taitung County') & (data['type']=='New Purchase')]['local_amt'].sum()

0.0

In [99]:
data

time                      type            city  epa_app  moea_app  \
0    2012-09-01              New Purchase     Taipei City      NaN      18.0   
1    2012-09-01  Elimination and Purchase     Taipei City      NaN      19.0   
2    2012-09-01               Elimination     Taipei City      NaN       0.0   
3    2012-09-01              New Purchase   Taichung City      NaN      45.0   
4    2012-09-01  Elimination and Purchase   Taichung City      NaN      45.0   
...         ...                       ...             ...      ...       ...   
3560 2019-12-01  Elimination and Purchase   Kinmen County     19.0      18.0   
3561 2019-12-01              New Purchase   Yunlin County    793.0    1151.0   
3562 2019-12-01  Elimination and Purchase   Yunlin County     92.0     134.0   
3563 2019-12-01              New Purchase  Kaohsiung City   1641.0    3583.0   
3564 2019-12-01  Elimination and Purchase  Kaohsiung City    184.0     402.0   

      moea_amt  epa_amt  local_amt  
0        10000      NaN        NaN  
1        10000      NaN        NaN  
2        10000      NaN        NaN  
3        10000      NaN        NaN  
4        10000      NaN        NaN  
...        ...      ...        ...  
3560     10000   5000.0    32000.0  
3561     10000   3000.0     9500.0  
3562     10000   5000.0    15000.0  
3563     10000   3000.0     4000.0  
3564     10000   5000.0    10000.0  

[3565 rows x 8 columns]